<a href="https://colab.research.google.com/github/Cezari0o/PLN-Trab/blob/main/a3/Atividade3_PLN.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Atividade 3
Feito por Gabriel Cesário Silva Martins - 180100912

## Recuperando o corpus de notícias

In [1]:
import nltk
import pandas as pd

nltk.download('reuters')
from nltk.corpus import reuters

cats = reuters.categories()
print("Reuters has %d categories:\n%s" % (len(cats), cats))

fileids = reuters.fileids()

[nltk_data] Downloading package reuters to /root/nltk_data...
[nltk_data]   Package reuters is already up-to-date!


Reuters has 90 categories:
['acq', 'alum', 'barley', 'bop', 'carcass', 'castor-oil', 'cocoa', 'coconut', 'coconut-oil', 'coffee', 'copper', 'copra-cake', 'corn', 'cotton', 'cotton-oil', 'cpi', 'cpu', 'crude', 'dfl', 'dlr', 'dmk', 'earn', 'fuel', 'gas', 'gnp', 'gold', 'grain', 'groundnut', 'groundnut-oil', 'heat', 'hog', 'housing', 'income', 'instal-debt', 'interest', 'ipi', 'iron-steel', 'jet', 'jobs', 'l-cattle', 'lead', 'lei', 'lin-oil', 'livestock', 'lumber', 'meal-feed', 'money-fx', 'money-supply', 'naphtha', 'nat-gas', 'nickel', 'nkr', 'nzdlr', 'oat', 'oilseed', 'orange', 'palladium', 'palm-oil', 'palmkernel', 'pet-chem', 'platinum', 'potato', 'propane', 'rand', 'rape-oil', 'rapeseed', 'reserves', 'retail', 'rice', 'rubber', 'rye', 'ship', 'silver', 'sorghum', 'soy-meal', 'soy-oil', 'soybean', 'strategic-metal', 'sugar', 'sun-meal', 'sun-oil', 'sunseed', 'tea', 'tin', 'trade', 'veg-oil', 'wheat', 'wpi', 'yen', 'zinc']


In [2]:
categories = []
text = []

for file in fileids:
    categories.append(reuters.categories(file))
    text.append(reuters.raw(file))

df = pd.DataFrame({'ids':fileids, 'categories':categories, 'text':text})

In [3]:
df

ids                                      categories  \
0         test/14826                                         [trade]   
1         test/14828                                         [grain]   
2         test/14829                                [crude, nat-gas]   
3         test/14832  [corn, grain, rice, rubber, sugar, tin, trade]   
4         test/14833                             [palm-oil, veg-oil]   
...              ...                                             ...   
10783   training/999                            [interest, money-fx]   
10784  training/9992                                          [earn]   
10785  training/9993                                          [earn]   
10786  training/9994                                          [earn]   
10787  training/9995                                          [earn]   

                                                    text  
0      ASIAN EXPORTERS FEAR DAMAGE FROM U.S.-JAPAN RI...  
1      CHINA DAILY SAYS VERMIN EAT 7-12 PCT GRAIN STO...  
2      JAPAN TO REVISE LONG-TERM ENERGY DEMAND DOWNWA...  
3      THAI TRADE DEFICIT WIDENS IN FIRST QUARTER\n  ...  
4      INDONESIA SEES CPO PRICE RISING SHARPLY\n  Ind...  
...                                                  ...  
10783  U.K. MONEY MARKET SHORTAGE FORECAST REVISED DO...  
10784  KNIGHT-RIDDER INC &lt;KRN> SETS QUARTERLY\n  Q...  
10785  TECHNITROL INC &lt;TNL> SETS QUARTERLY\n  Qtly...  
10786  NATIONWIDE CELLULAR SERVICE INC &lt;NCEL> 4TH ...  
10787  &lt;A.H.A. AUTOMOTIVE TECHNOLOGIES CORP> YEAR ...  

[10788 rows x 3 columns]

## Funções de Suporte

In [4]:
import re

def preprocessing(text):
    t = re.sub(r'#','',text)
    t = t.lower()
    t = re.sub(r'[\,\.\'\$\!/"\(\)\-<>]+',' ',t)
    t = re.sub(r'\\u2019', '\'', t)
    t = re.sub(r'\\u002c', ',', t)
    t = re.sub(r'&lt;', ' ', t)
    t = re.sub(r':\)','happy', t)
    
    return t

In [5]:
def calc_prod_interno(b1: dict, b2: dict):
  prod_interno = 0

  # repeated_words = set()

  for w in b1.keys():
    if w in b2:
      prod_interno += b1[w] * b2[w]
      # repeated_words.add(w)

  # for w in b2.keys():
  #   if w in b1 and w not in repeated_words:
  #     prod_interno += b1[w] * b2[w]

  return prod_interno

In [6]:
def calc_norma(v: dict):
  norma = 0

  for n in v:
    norma += v[n]**2
  norma = norma**0.5

  return norma

In [7]:
def cos_dissimilarity(v1: dict, v2: dict):

  pi = calc_prod_interno(v1, v2)
  
  return pi / (calc_norma(v1)*calc_norma(v2))

## Preparando a execução

### Criando bag of words

E também o vocabulário do corpus.

In [9]:
vocab = set()

for txt in df['text']:
    txt = preprocessing(txt)

    for term in txt.split():
        vocab.add(term)

vocab = sorted(vocab)
print(len(vocab))

31150


In [10]:
bow_pond = {}
quant_words = {}

for idx, linha in df.iterrows():

  frase = linha['text']
  doc = linha['ids']
  bow_pond[doc] = dict()

  frase = preprocessing(frase)
  quant_words[doc] = len(frase.split())

  for w in frase.split():
    if w in bow_pond[doc]:
      bow_pond[doc][w] += 1
    else:
      bow_pond[doc][w] = 1

for doc in bow_pond:
  for w in bow_pond[doc]:
    bow_pond[doc][w] /= quant_words[doc]


In [11]:
bow_cont = {}

for idx, linha in df.iterrows():

  frase = linha['text']
  doc = linha['ids']
  bow_cont[doc] = dict()

  frase = preprocessing(frase)
  for w in frase.split():
    if w in bow_cont[doc]:
      bow_cont[doc][w] += 1
    else:
      bow_cont[doc][w] = 1

In [ ]:
idf = {}

for word in vocab:
    idf[word] = 0
    # contabilizar em quantos documentos a palavra word aparece
    for doc in bow_cont:
        if word in bow_cont[doc]:
            idf[word] += 1

from math import log

for w in idf:
  idf[w] = log(len(df)/idf[w])
idf

In [13]:
bow_tfidf = {}

for doc in bow_pond:
  bow_tfidf[doc] = {}
  for w in bow_pond[doc]:
    bow_tfidf[doc][w] = bow_pond[doc][w] * idf[w]

bow_tfidf

{'test/14826': {'1': 0.0012129835850540056,
  '10': 0.0024142885436470697,
  '15': 0.0027078951530582467,
  '17': 0.003382981983184548,
  '1985': 0.003142601372964703,
  '30': 0.0027836800262065397,
  '300': 0.00441427550366519,
  '4': 0.0019500399054040776,
  '53': 0.005022809302541407,
  '6': 0.0021342866299050296,
  '7': 0.0021232078345189594,
  '9': 0.0022951785216275824,
  '95': 0.00505664963907546,
  'a': 0.010664870396794536,
  'able': 0.005644884490776457,
  'accounting': 0.005956109715050271,
  'action': 0.004508696139365563,
  'advantage': 0.007061979867058442,
  'against': 0.009570136594487208,
  'alleged': 0.01440085990667359,
  'allow': 0.01054714881917444,
  'also': 0.009450176972931369,
  'american': 0.003918187755371405,
  'among': 0.009760934696667164,
  'an': 0.003541097072549645,
  'analyst': 0.005293947847873639,
  'and': 0.009811766489455604,
  'any': 0.003595977584790815,
  'april': 0.002614686485526545,
  'are': 0.011567343687372438,
  'as': 0.003966452775130563,

In [27]:
bow_bin = dict()

i = 0
for idx, linha in df.iterrows():

  frase = linha['text']
  doc = linha['ids']
  i += 1
  bow_bin[doc] = dict()

  frase = preprocessing(frase)
  for w in frase.split():
    bow_bin[doc][w] = 1

bow_bin

{'test/14826': {'1': 1,
  '10': 1,
  '15': 1,
  '17': 1,
  '1985': 1,
  '30': 1,
  '300': 1,
  '4': 1,
  '53': 1,
  '6': 1,
  '7': 1,
  '9': 1,
  '95': 1,
  'a': 1,
  'able': 1,
  'accounting': 1,
  'action': 1,
  'advantage': 1,
  'against': 1,
  'alleged': 1,
  'allow': 1,
  'also': 1,
  'american': 1,
  'among': 1,
  'an': 1,
  'analyst': 1,
  'and': 1,
  'any': 1,
  'april': 1,
  'are': 1,
  'as': 1,
  'asia': 1,
  'asian': 1,
  'asked': 1,
  'association': 1,
  'at': 1,
  'australia': 1,
  'australian': 1,
  'avowed': 1,
  'awaiting': 1,
  'aware': 1,
  'barriers': 1,
  'be': 1,
  'because': 1,
  'beef': 1,
  'been': 1,
  'below': 1,
  'between': 1,
  'beyond': 1,
  'biggest': 1,
  'billion': 1,
  'block': 1,
  'boost': 1,
  'broker': 1,
  'budget': 1,
  'business': 1,
  'businessmen': 1,
  'but': 1,
  'button': 1,
  'by': 1,
  'call': 1,
  'canberra': 1,
  'capel': 1,
  'capitals': 1,
  'centred': 1,
  'chairman': 1,
  'chief': 1,
  'co': 1,
  'coal': 1,
  'commercial': 1,
  'com

### Ranking de similaridade

Criando o ranking para cada notícia.

In [15]:
def get_rank(bow, lim = None):
  similarity_rank = dict()

  for idx, doc in enumerate(bow):

    if idx >= lim:
      break

    similarity_rank[doc] = 10 * [(None, 0)]

  for entry_count, doc in enumerate(bow):

    # print(bow[doc]); break
    if lim and entry_count >= lim:
      break

    for inner_count, doc_query in enumerate(bow):

      if lim and inner_count >= lim:
        break

      if doc != doc_query:

        similarity = cos_dissimilarity(bow[doc], bow[doc_query])      

        # Ranqueando
        r = 10
        for id, sim_val in reversed(similarity_rank[doc]):
          if similarity > sim_val:
            r -= 1
          else:
            break
        if r < 10:
          similarity_rank[doc] = similarity_rank[doc][:r] + [(doc_query, similarity)] + similarity_rank[doc][r:-1]

  return similarity_rank

In [17]:
rank_tfidf = get_rank(bow_tfidf, 5000)

In [ ]:
rank_tfidf

In [19]:
rank_bow_bin = get_rank(bow_bin, 5000)

In [ ]:
rank_bow_bin

## Ranking de Acurácia
Calculando o ranking de acurácia

In [22]:
def get_accuracy(rank_similarity: dict):
  
  top10 = dict()
  for i in range(0, 10):
    top10[i] = 0

  for doc in rank_similarity:
    idx_doc = df.index[df['ids'] == doc][0]

    for idx, d in enumerate(rank_similarity[doc]): # d == tupla -> (documento, similaridade)
      idx_d = df.index[df['ids'] == d[0]][0]

      for cat in df.at[idx_d, 'categories']:
        if cat in df.at[idx_doc, 'categories']:
          top10[idx] += 1
          break

  return top10

### Ranking BoW

In [24]:
top10_bow = get_accuracy(rank_bow_bin)
top10_bow

{0: 4347,
 1: 4148,
 2: 4012,
 3: 3953,
 4: 3878,
 5: 3811,
 6: 3767,
 7: 3750,
 8: 3700,
 9: 3658}

### Ranking TF-IDF

In [25]:
top10_tfidf = get_accuracy(rank_tfidf)
top10_tfidf

{0: 4229,
 1: 4000,
 2: 3956,
 3: 3922,
 4: 3935,
 5: 3846,
 6: 3853,
 7: 3729,
 8: 3742,
 9: 3703}